# Diet optimization problem

# 1. Introduction

Although in the modern world dieting is a hot and widespread topic due to the implications it has 
on health ([obesity pandemic](https://www.ncbi.nlm.nih.gov/pmc/articles/PMC9107388/pdf/main.pdf)) 
and aesthetics (especially as [social media constantly convey unrealistic expectations around body image](https://www.ualberta.ca/human-resources-health-safety-environment/news/2022/01-january/february-2022-life-lines.html)), 
this blog post will reduce its discussion and analysis to the mathematical formulations that can 
rise from the challenge of choosing *what* and *how much* to eat given different criteria/objectives.

My first encounter with this problem was in [Boyd's book](https://web.stanford.edu/~boyd/cvxbook/bv_cvxbook.pdf) 
(pg. 162), where the objective is to build a diet that contains enough nutrients to be a healthy 
one but is the cheapest possible. What does the "but" in the last sentence for? Because the 
cheapest diet without restrictions is to eat nothing &#129313;. 

For this study, the dataset used comes from [this page](https://developers.google.com/optimization/lp/stigler_diet), 
the daily intake can be found in `./data/daily_intake.csv` on the [code repository](https://github.com/RomuloDrumond/diet-optimization-problem).

You can take a look at the data on the following cell:

In [1]:
import pandas as pd

df = pd.read_csv('./data/stigler.csv')
print("df:")
display(df)

daily_intake = pd.read_csv('./data/daily_intake.csv')
print("daily_intake:")
display(daily_intake)

df:


commodity    unit  price_cents  calories_k  protein_g  \
0    Wheat Flour (Enriched)  10 lb.         36.0        44.7       1411   
1                  Macaroni   1 lb.         14.1        11.6        418   
2   Wheat Cereal (Enriched)  28 oz.         24.2        11.8        377   
3               Corn Flakes   8 oz.          7.1        11.4        252   
4                 Corn Meal   1 lb.          4.6        36.0        897   
..                      ...     ...          ...         ...        ...   
72                Chocolate   8 oz.         16.2         8.0         77   
73                    Sugar  10 lb.         51.7        34.9          0   
74               Corn Syrup  24 oz.         13.7        14.7          0   
75                 Molasses  18 oz.         13.6         9.0          0   
76     Strawberry Preserves   1 lb.         20.5         6.4         11   

    calcium_g  iron_mg  vitamin_a_kiu  vitamin_b1_mg  vitamin_b2_mg  \
0         2.0      365            0.0           55.4           33.3   
1         0.7       54            0.0            3.2            1.9   
2        14.4      175            0.0           14.4            8.8   
3         0.1       56            0.0           13.5            2.3   
4         1.7       99           30.9           17.4            7.9   
..        ...      ...            ...            ...            ...   
72        1.3       39            0.0            0.9            3.4   
73        0.0        0            0.0            0.0            0.0   
74        0.5       74            0.0            0.0            0.0   
75       10.3      244            0.0            1.9            7.5   
76        0.4        7            0.2            0.2            0.4   

    niacin_mg  vitamin_c_mg  
0         441             0  
1          68             0  
2         114             0  
3          68             0  
4         106             0  
..        ...           ...  
72         14             0  
73          0             0  
74          5             0  
75        146             0  
76          3             0  

[77 rows x 12 columns]

daily_intake:


nutrient  daily_recommended_intake        unit
0    Calories                       3.0  k Calories
1     Protein                      70.0           g
2     Calcium                       0.8           g
3        Iron                      12.0          mg
4   Vitamin A                       5.0         KIU
5  Vitamin B1                       1.8          mg
6  Vitamin B2                       2.7          mg
7      Niacin                      18.0          mg
8   Vitamin C                      75.0          mg

As data preprocessing steps we took `df` and:
* Split the "unit" column between "qtd" and the true "unit";
* Normalized the rows to contain the price and nutrients for 1 unit value of the true "unit" column;
* Applied accumulated inflation between 1939 and 2022 ([this site was used](https://www.in2013dollars.com/us/inflation/1939?amount=1)).
  Although food price differences between 83 years are more complex than applying inflation, we used this simplification just to have an idea of what the price of the diets would be in today's economy.

If you want to see the code go to the [GitHub repository](https://github.com/RomuloDrumond/diet-optimization-problem).


In [2]:
from dietoptproblem.preprocess import apply_preprocess

df_processed = apply_preprocess(df)
print("df_processed:")
df_processed

df_processed:


commodity unit        USD  calories_k   protein_g  \
0    Wheat Flour (Enriched)  lb.   7.718292    4.470000  141.100000   
1                  Macaroni  lb.   3.022998   11.600000  418.000000   
2   Wheat Cereal (Enriched)  oz.   5.188407    0.421429   13.464286   
3               Corn Flakes  oz.   1.522219    1.425000   31.500000   
4                 Corn Meal  lb.   0.986226   36.000000  897.000000   
..                      ...  ...        ...         ...         ...   
72                Chocolate  oz.   3.473231    1.000000    9.625000   
73                    Sugar  lb.  11.084325    3.490000    0.000000   
74               Corn Syrup  oz.   2.937239    0.612500    0.000000   
75                 Molasses  oz.   2.915799    0.500000    0.000000   
76     Strawberry Preserves  lb.   4.395138    6.400000   11.000000   

    calcium_g    iron_mg  vitamin_a_kiu  vitamin_b1_mg  vitamin_b2_mg  \
0    0.200000  36.500000            0.0       5.540000       3.330000   
1    0.700000  54.000000            0.0       3.200000       1.900000   
2    0.514286   6.250000            0.0       0.514286       0.314286   
3    0.012500   7.000000            0.0       1.687500       0.287500   
4    1.700000  99.000000           30.9      17.400000       7.900000   
..        ...        ...            ...            ...            ...   
72   0.162500   4.875000            0.0       0.112500       0.425000   
73   0.000000   0.000000            0.0       0.000000       0.000000   
74   0.020833   3.083333            0.0       0.000000       0.000000   
75   0.572222  13.555556            0.0       0.105556       0.416667   
76   0.400000   7.000000            0.2       0.200000       0.400000   

     niacin_mg  vitamin_c_mg  
0    44.100000           0.0  
1    68.000000           0.0  
2     4.071429           0.0  
3     8.500000           0.0  
4   106.000000           0.0  
..         ...           ...  
72    1.750000           0.0  
73    0.000000           0.0  
74    0.208333           0.0  
75    8.111111           0.0  
76    3.000000           0.0  

[77 rows x 12 columns]

As now we have the data, the mathematical formulation may be clearer.

Our diet must contain $m$ nutrients with at least $b_1$, . . . , $b_m$ quantities, as you may see 
on the `daily_intake` dataframe we have $m=9$ and our vector $b$ will be the values in column 
*daily_recommended_intake* of `daily_intake` dataframe. To build the diet we choose nonnegative quantities $x_1$, . . . , $x_n$ of
$n$ different foods, in our case $n=77$ which is the number of rows of our `df_processed` dataset. 
One unit quantity of food $j$ contains an amount $a_{ij}$ of nutrient
$i$ and has a cost of $c_j$ (note that the values in `df_processed` are the transpose of the following matrix $A$). 
We want to determine the cheapest diet, $x_{opt}$, that satisfies the nutritional requirements, `daily_recommended_intake`. This problem 
can be formulated as the linear program (LP):

$$
\begin{equation} \tag{1}
    \begin{split}
        \text{minimize } \ & c^tx \\
        \text{subject to } \ & Ax \succeq b \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

Where if $a, b \in \R^n_+$, $a \succeq b$ means that $\forall i = 1, . . . , n \implies a_i \ge b_i$.

# 2. Finding the optimal diet

Now that we have the data and the mathematical formulation, we can model the problem and find
the "optimal" diet given our criteria (the objective function). To do so, we will use [CVXPY](https://www.cvxpy.org/index.html),
a python package for solving convex problems. Although our problem is a linear one and CVXPY maybe 
feel like overkill, as linear problems are convex ones, this library is a more general tool than using a linear solver, 
meaning that we can keep using the same tool for other non-linear problems.

The following code uses CVXPY to solve the problem (1):

In [3]:
import cvxpy as cp

# Problem data
c = df_processed.USD.values
A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values

# Constructing the problem
x = cp.Variable(shape=len(c))
objective = cp.Minimize(c@x)
constraints = [
    A@x >= b,
    x >= 0,
]
problem = cp.Problem(objective=objective, constraints=constraints)

result = problem.solve()
# The solution
print(f"{result = }")
print(f"{x.value = }")

result = 0.15360703766856018
x.value = array([-3.76573316e-14,  8.68348920e-14, -1.46738328e-13,  8.13624289e-14,
        5.34424634e-03,  2.95446061e-14,  3.06770764e-13,  4.37997030e-13,
        2.77853882e-13,  2.04462612e-13,  1.77817196e-13, -1.69845507e-14,
        6.44932975e-14,  3.49824397e-13,  9.76998354e-14, -7.88504668e-14,
        2.33506059e-14, -1.23905986e-14,  4.03105827e-14,  4.02896389e-14,
        1.10932580e-13, -1.13920983e-14, -4.78824654e-14,  2.04427572e-13,
       -3.59915089e-14, -2.24149401e-14, -1.19513449e-14,  2.23277626e-14,
        7.37335280e-14,  5.53354150e-14, -1.12987895e-15, -3.96683084e-14,
       -6.50090199e-15,  1.99263707e-14, -1.15558487e-14, -2.94876516e-15,
        4.50554631e-14, -1.87698517e-14, -4.19150510e-14, -2.37919029e-14,
        4.57123757e-13,  2.85788206e-13,  2.81256178e-14,  3.21319703e-14,
        2.43133822e-13,  1.13132451e-02,  4.68001567e-13,  1.77437607e-13,
        1.82422902e-13,  8.41262040e-13, -4.33849115e-14,  5.

Translating the numbers, or the $x$ vector, of our problem, the optimal diet (**weekly** to make the numbers more
readable) would be:

In [4]:
from dietoptproblem.utils import compute_diet_df

print(f"Cost: {result*7:.2f} USD/week")

df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
df_diet

Cost: 1.08 USD/week


commodity  qtd_weekly  usd_weekly
0  Navy Beans, Dried  0.7215 lb.        0.91
1            Cabbage  0.0792 lb.        0.06
2            Spinach  0.0362 lb.        0.06
3          Corn Meal  0.0374 lb.        0.04

Ok ok, a diet that give us enough nutrients and costs 1.08 USD/week seems pretty 
cheap, as was stated from the optimization problem. But, looking the menu... just 
4 things will be eating? Yeah... this does not seem like a diverse diet that I'll be
able to stick to. **Can I modeled something like diversity on my diet?**

In [5]:
x = cp.Variable(shape=len(c))
objective = cp.Minimize(
    c@x 
    + 10*cp.norm(x,2)**2 
)
constraints = [x >= 0, A@x >= b]
problem = cp.Problem(objective=objective, constraints=constraints)
result = problem.solve()

print(f"Cost: {result*7:.2f} USD/week")

df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
df_diet

Cost: 1.48 USD/week


commodity  qtd_weekly  usd_weekly
0  Navy Beans, Dried  0.3731 lb.        0.47
1  Lima Beans, Dried  0.1857 lb.        0.35
2          Corn Meal  0.1935 lb.        0.19
3            Cabbage  0.0785 lb.        0.06
4            Spinach  0.0234 lb.        0.04
5        Peas, Dried  0.0169 lb.        0.03
6     Sweet Potatoes  0.0205 lb.        0.02

The little trick applied above was to add norm 2 regularization to the $x$ variable, the new optimization problem would be:


$$
\begin{equation} \tag{2}
    \begin{split} 
        \text{minimize } \ & c^tx + 10\lVert x \rVert _2^2\\ 
        \text{subject to } \ & Ax \succeq b \\
                             & x \succeq 0 
   \end{split}
\end{equation}
$$



But why the $l_2$-norm was applied? In a nutshell, if you derive the $\lVert x \rVert _2^2$ by some component of $x$, like $x_i$, you will find 

$$
\frac{\partial}{\partial x_i} \lVert x \rVert _2^2 = 2x_i
$$

Meaning that bigger is $x_i$ biggest is the incentive (derivative) to decrease it's value on the objective function. As $x_i$ gets close to zero the incentive decreases too, meaning, in pratical terms, that we penalize big (relative) values and don't care too much with small ones. That would be something like: *"I want a cheap diet but don't want to just eat one thing, as I want some variety, even if I can eat just a little"*.

Note: where does this random $10$ come from? It was acquire buy try-and-error until a found a more diverse diet that didn't cost too much (find the balance between both objectives).

# 3. What was the problem again?

An interesting thing happend by the end of previous section: we noted that *our objective wasn't really aligned with what we wanted*. This is an important conclusion that you might not see much value, but we real life **we often see this misaligment between the mathematical formulation and the business need**. When this misaligment happens, **solving the optimization problem does not translate in solving the real world problem**.

So, initially we wanted a diet that had all the necessary nutrients while being cheap as possible (see Eq. 1), but, what if, we were looking for getting lean, what would happen?

## 3.1 Trying to get shredded

This time we want to minimize our calories while ingest enough of the 
other nutrients. The $\sigma$ vector represent how much calories each
food contains.

$$
\begin{equation} \tag{3}
    \begin{split}
        \text{minimize } \ & \sigma^tx \\
        \text{subject to } \ & Ax \succeq b_{\sigma} \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

On equation 3, $b_{\sigma}$ is the modified version of our `daily_intake`
where the minimum value for calories is $0$ (zero).


In [6]:
import numpy as np

A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
b[0] = 0 # no need for calories constraint
calories = df_processed.calories_k.values

x = cp.Variable(shape=len(calories))
objective = cp.Minimize(calories@x)
constraints = [x >= 0, A@x >= b]
problem = cp.Problem(objective=objective, constraints=constraints)

result = problem.solve()
print(f"Calories: {result:.2f} kcal/day")

cost = df_processed.USD.values
print(f"Cost: {np.dot(cost, x.value)*7:.2f} USD/week")
df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
df_diet

Calories: 0.60 kcal/day
Cost: 39.93 USD/week


commodity    qtd_weekly  usd_weekly
0  Salmon, Pink (can)    6.5861 oz.       18.36
1              Coffee    3.3034 lb.       15.86
2        Liver (Beef)    0.4617 lb.        2.65
3                 Tea    0.4397 lb.        1.64
4              Celery  0.9029 stalk        1.41

It would be a more expensive diet but with really small quantity of calories daily, only 600 cal.

Disclaimer: please, remember this is a mathematical exercise, not a real diet, don't be dumb and just
eat salmon for now on.

## 3.2 Could we add "tastyness" to the mix?

Thinking about dieting we may realize that one of the big challenges of it is that people need to
change their eating habits, meaning, they end up eating what they don't like. So, let's add a 
new column to our data set with the "tastyness" of the commodities, ranging from -5, "*I really*
*dispise it*", to +5, "*If I could, I would eat this every day*".

To avoid eating too much we also added an upper bound to the nutrients in 
the diet (which include calories, the probably big affect by my tastynees 
preferences 😁). The $\tau$ letter will represent the vector of the tastyness
of each commoditie.

$$
\begin{equation} \tag{4}
    \begin{split}
        \text{minimize } \ & -\tau^tx \\
        \text{subject to } \ & Ax \succeq b \\
                             & Ax \preceq 1.2b \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

PS: The negative signal on the objective function of Eq. 4 is to translate
the tastyness maximization problem to a minimization one.

tastyness               commoditie
0           0   Wheat Flour (Enriched)
1           3                 Macaroni
2           2  Wheat Cereal (Enriched)
3           3              Corn Flakes
4           0                Corn Meal
..        ...                      ...
72          5                Chocolate
73          0                    Sugar
74         -2               Corn Syrup
75          3                 Molasses
76          3   "Strawberry Preserves"

[77 rows x 2 columns]

In [20]:
tastyness_df = pd.read_csv('./data/tastyness_by_romulo.csv')
tastyness_df

tastyness               commoditie
0           0   Wheat Flour (Enriched)
1           3                 Macaroni
2           2  Wheat Cereal (Enriched)
3           3              Corn Flakes
4           0                Corn Meal
..        ...                      ...
72          5                Chocolate
73          0                    Sugar
74         -2               Corn Syrup
75          3                 Molasses
76          3   "Strawberry Preserves"

[77 rows x 2 columns]

In [21]:
A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
tastyness = tastyness_df['tastyness'].values

x = cp.Variable(shape=len(calories))
objective = cp.Minimize(-tastyness@x)
constraints = [
    x >= 0, 
    A@x >= b, 
    A@x <= 1.2*b
]
problem = cp.Problem(objective=objective, constraints=constraints)

result = problem.solve()
print(f"{result = }")
calories = df_processed.calories_k.values
print(f"Calories: {np.dot(calories, x.value):.2f} k/day")

cost = df_processed.USD.values
print(f"Cost: {np.dot(cost, x.value)*7:.2f} USD/week")
df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
df_diet

result = -12.753855640167885
Calories: 3.60 k/day
Cost: 71.15 USD/week


commodity        qtd_weekly  usd_weekly
0              Chocolate       13.4992 oz.       46.89
1        Pineapple (can)  1.2057 No. 2 1/2        5.51
2  Evaporated Milk (can)        3.1825 oz.        4.57
3            Leg of Lamb        0.6486 lb.        3.84
4     Salmon, Pink (can)        1.3280 oz.        3.70
5                 Coffee        0.6892 lb.        3.31
6                 Butter        0.3695 lb.        2.44
7             Pork Chops        0.1338 lb.        0.88
8                Spinach        0.0112 lb.        0.02

Wooww, **71.15 USD/week** is kind expensive, couldn't we add the cost to the objective function so 
we could control it a bit?

The new problem formulation would be:


$$
\begin{equation} \tag{5}
    \begin{split}
        \text{minimize } \ & -\tau^tx + c^tx\\
        \text{subject to } \ & Ax \succeq b \\
                             & Ax \preceq 1.2b \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

In [8]:
A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
c = df_processed.USD.values

x = cp.Variable(shape=len(calories))
objective = cp.Minimize(c@x - tastyness@x)
constraints = [x >= 0, A@x >= b, A@x <= 1.2*b]
problem = cp.Problem(objective=objective, constraints=constraints)

result = problem.solve()
print(f"{result = }")
calories = df_processed.calories_k.values
print(f"Calories: {np.dot(calories, x.value):.2f} k/day")

cost = df_processed.USD.values
print(f"Cost: {np.dot(cost, x.value)*7:.2f} USD/week")
df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
df_diet

result = -3.888757761956829
Calories: 3.07 k/day
Cost: 44.21 USD/week


commodity    qtd_weekly  usd_weekly
0              Chocolate    7.0156 oz.       24.37
1            Corn Flakes    7.0783 oz.       10.77
2  Evaporated Milk (can)    4.9459 oz.        7.10
3                    Tea    0.3031 lb.        1.13
4             Corn (can)  0.2390 No. 2        0.53
5           Liver (Beef)    0.0367 lb.        0.21
6                Cabbage    0.0714 lb.        0.06
7                Spinach    0.0180 lb.        0.03

Ok ok, 44.21 USD/week seems more reasonable. As an effect of adding the cost in our objective 
function we got ride of Pineapple that altough I like it (+5 in tastyness) it seems a bit expensive
compared to others. Because we now consider cost, Liver also get in my diet athough I'm not such a 
big fan (-2 in tastyness).

Now we have an interesting problem: as we have two objectives in the same objective function, they
might compete. Do they compete? We can test it by optimizing for each objective separetely:

In [9]:
A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
c = df_processed.USD.values

x = cp.Variable(shape=len(calories))
constraints = [x >= 0, A@x >= b, A@x <= 1.2*b]

objectives_dict = {
    "Cost": cp.Minimize(c@x),
    "Tastyness": cp.Minimize(-tastyness@x),
} 
for tag, objective_function in objectives_dict.items():
    print(f"Solving for: {tag}")
    problem = cp.Problem(objective=objective_function, constraints=constraints)

    result = problem.solve()
    print(f"{result = }")
    calories = df_processed.calories_k.values
    print(f"Calories: {np.dot(calories, x.value):.2f} k/day")

    cost = df_processed.USD.values
    print(f"Cost: {np.dot(cost, x.value)*7:.2f} USD/week")
    df_diet = compute_diet_df(df=df_processed, qtds=x.value.tolist())
    display(df_diet)
    
    print('\n')


Solving for: Cost
result = 0.3957707708368031
Calories: 3.00 k/day
Cost: 2.77 USD/week


commodity  qtd_weekly  usd_weekly
0            Liver (Beef)  0.1466 lb.        0.84
1                    Milk  0.3343 qt.        0.79
2  White Bread (Enriched)  0.2973 lb.        0.50
3               Corn Meal  0.2758 lb.        0.27
4                    Lard  0.0712 lb.        0.15
5                  Onions  0.1580 lb.        0.12
6                 Cabbage  0.0571 lb.        0.05
7           Peanut Butter  0.0112 lb.        0.04



Solving for: Tastyness
result = -12.753855640167885
Calories: 3.60 k/day
Cost: 71.15 USD/week


commodity        qtd_weekly  usd_weekly
0              Chocolate       13.4992 oz.       46.89
1        Pineapple (can)  1.2057 No. 2 1/2        5.51
2  Evaporated Milk (can)        3.1825 oz.        4.57
3            Leg of Lamb        0.6486 lb.        3.84
4     Salmon, Pink (can)        1.3280 oz.        3.70
5                 Coffee        0.6892 lb.        3.31
6                 Butter        0.3695 lb.        2.44
7             Pork Chops        0.1338 lb.        0.88
8                Spinach        0.0112 lb.        0.02

As you can see, we have different results (different $x_{opt}$) depending on the objective.
We can visualize it in a 2D plane were each axis is an objective:

In [23]:
import plotly.express as px

A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
c = df_processed.USD.values

x = cp.Variable(shape=len(calories))
constraints = [x >= 0, A@x >= b, A@x <= 1.2*b]

objectives_dict = {
    "Cost": cp.Minimize(c@x),
    "Tastyness": cp.Minimize(-tastyness@x),
} 
x_list = []
y_list = []
for tag, objective_function in objectives_dict.items():
    problem = cp.Problem(objective=objective_function, constraints=constraints)
    result = problem.solve()

    cost = np.dot(c, x.value)
    tastyness_ = -np.dot(tastyness, x.value)

    x_list.append(cost)
    y_list.append(tastyness_)


fig = px.scatter(x=x_list, y=y_list)
size = 600
fig.update_layout(
    xaxis_title='Cost',
    yaxis_title='- Tastyness',
    width=size, height=size
)
fig.update_traces(marker=dict(size=20))
fig.show()

As you may see, we don't have a "perfect solution" where there the left-most point is the downwards-most point too.

To analyse the trade-off between the objectives we may give different weights for each objective
and explore the curve that lies between the graphs of the previous plot. Let do this!

# 4. Finding Pareto curve

For finding the pareto curve we will weight the objectives using the variable 
$\mu$, as you may see in Eq. 6.


$$
\begin{equation} \tag{6}
    \begin{split}
        \text{minimize } \ & -(1-\mu)\tau^tx + \mu c^tx\\
        \text{subject to } \ & Ax \succeq b \\
                             & Ax \preceq 1.2b \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

The variable $\mu$ will assume many values between $[0,1]$ so we can see
the trade-off between the two objectives.

In [11]:
from tqdm.notebook import tqdm

A = df_processed.iloc[:, 3:].T.values
b = daily_intake.daily_recommended_intake.values.copy()
c = df_processed.USD.values

mu_list = [0] + np.logspace(-5, 0, num=1_000).tolist()

x = cp.Variable(shape=len(calories))
constraints = [x >= 0, A@x >= b, A@x <= 1.2*b]

cost_list = []
tastyness_list = []
for mu in tqdm(mu_list):
    objective_function = cp.Minimize(mu*c@x - (1 - mu)*tastyness@x)
    problem = cp.Problem(objective=objective_function, constraints=constraints)
    result = problem.solve()

    cost = np.dot(c, x.value)
    tastyness_ = -np.dot(tastyness, x.value)

    cost_list.append(cost)
    tastyness_list.append(tastyness_)

  0%|          | 0/1001 [00:00<?, ?it/s]

In [12]:
import plotly.graph_objects as go

fig = go.Figure(go.Scatter(x=cost_list, y=tastyness_list, mode='lines'))
size = 600
fig.update_layout(
    title='Pareto curve',
    xaxis_title='Cost',
    yaxis_title='- Tastyness',
    width=size, height=size,
)
fig.update_xaxes(range=[0, 11])


fig.show()

So, what does this line means? For every point in this line there is not other feaseable point that, 
simultanesly, reduces **cost** and **-tastyness** at the same time, meaning, choosing a point in this line
means you had made a trade-off between cost and tastyness.

As one outstanding professor once said during my undergraduate studies "Life is a small blanket: 
you cover your head and you end up uncovering your feet, you cover your feet and you end up 
uncovering your head". Meaning, on multi-objective optimization problems in real life the 
objectives always end up competing, there is no "solution to rule them all", you will often need
to choose a trade-off between objectives.

Does the pareto curve only exist in 2D? No, but for visualizing it we usually stop in 3D. As an 
example, let's add minimization of calories as a third objective:

$$
\begin{equation} \tag{7}
    \begin{split}
        \text{minimize } \ & \mu_0 c^tx - \mu_1\tau^tx + \mu_2\sigma^t*x\\
        \text{subject to } \ & Ax \succeq b \\
                             & Ax \preceq 1.2b \\
                             & x \succeq 0
   \end{split}
\end{equation}
$$

In Eq. 7 the variables $\mu_0$, $\mu_1$ and $\mu_2$ will assume many values between 
$[0,1]$ so we can build the pareto surface.

In [13]:
import itertools

A = df_processed.iloc[:, 3:].T.values
b_with_calories = daily_intake.daily_recommended_intake.values.copy()
b = daily_intake.daily_recommended_intake.values.copy()
b[0] = 0 # no need for lower bound calories constraint
calories = df_processed.calories_k.values
c = df_processed.USD.values

n_points = 25
mu0 = [0] + np.logspace(-5, 0, num=n_points-1).tolist()
mu1 = [0] + np.logspace(-5, 0, num=n_points-1).tolist()
mu2 = [0] + np.logspace(-5, 0, num=n_points-1).tolist()

x = cp.Variable(shape=len(calories))
constraints = [x >= 0, A@x >= b, A@x <= 1.2*b_with_calories]

def optimize_diet(mu0, mu1, mu2):
    objective_function = cp.Minimize(mu0*c@x - mu1*tastyness@x + mu2*calories@x)
    problem = cp.Problem(objective=objective_function, constraints=constraints)
    result = problem.solve()

    cost = np.dot(c, x.value)
    tastyness_ = -np.dot(tastyness, x.value)
    calories_ = np.dot(calories, x.value)

    return cost, tastyness_, calories_


from joblib import Parallel, delayed

results = Parallel(n_jobs=-1)(delayed(optimize_diet)(mu0, mu1, mu2) for mu0, mu1, mu2 in tqdm(list(itertools.product(mu0, mu1, mu2))))

cost_list = [tuple_[0] for tuple_ in results]
tastyness_list = [tuple_[1] for tuple_ in results]
calories_list = [tuple_[2] for tuple_ in results]

  0%|          | 0/15625 [00:00<?, ?it/s]

In [14]:
import scipy.interpolate as interp

mesh_n_points = 200
x, y = np.meshgrid(
    np.linspace(min(cost_list), max(cost_list), num=mesh_n_points), 
    np.linspace(min(tastyness_list), max(tastyness_list), num=mesh_n_points),
)

z = interp.griddata(
    points=(cost_list, tastyness_list),
    values=calories_list,
    xi=(x, y),
    method='linear'
)
fig = go.Figure(data=go.Surface(
    x=x,
    y=y,
    z=z,
    opacity=0.95
))
fig.update_layout(
    title="Pareto 3D curve",
    height=1000,
    scene = dict(
        xaxis_title = "Cost (x)",
        yaxis_title = "-Tastyness (y)",
        zaxis_title = "Calories (z)",
    )
)
fig.show()

# 5. Final thoughts

Altough this diet optimization problem is well know and used for academic pourposes, my objective 
with this blog post is to show the reader that **defining the objetive** and **translating it** 
**mathematically** are not always easy tasks, and, as most problems in real life, we will have 
competing objectives, meaning, **choosing a trade-off between the multiple objectives** is added to
this already complex task. 

That's it! I hope this was informative and made you think about proper setting objectives in your
optimization problems. :muscle: